# Query database

Notebook for running Python sqlite3 commands for querying database.

Specific code blocks run separately to produce statistics.

## Setup:

In [1]:
import matplotlib.pyplot as plt
import numpy as np

In [2]:
import sqlite3

In [3]:
# path on rte
db_path = "/home/rte/data/db/arxiv_db_images.sqlite3"

In [4]:
# Here we import the sqlite3 database and create a cursor

db = sqlite3.connect(db_path)
c = db.cursor()

Get the pragma table info for each table

In [5]:
c.execute('PRAGMA TABLE_INFO({})'.format("metadata"))
info = c.fetchall()

print("\nColumn Info:\nID, Name, Type, NotNull, DefaultVal, PrimaryKey")
for col in info:
    print(col)


Column Info:
ID, Name, Type, NotNull, DefaultVal, PrimaryKey
(0, 'id', 'INTEGER', 0, None, 1)
(1, 'identifier', 'TEXT', 0, None, 0)
(2, 'created', 'TEXT', 0, None, 0)
(3, 'cat', 'TEXT', 0, None, 0)
(4, 'authors', 'TEXT', 0, None, 0)
(5, 'title', 'TEXT', 0, None, 0)
(6, 'abstract', 'TEXT', 0, None, 0)
(7, 'licence', 'TEXT', 0, None, 0)


In [6]:
c.execute('PRAGMA TABLE_INFO({})'.format("images"))
info = c.fetchall()

print("\nColumn Info:\nID, Name, Type, NotNull, DefaultVal, PrimaryKey")
for col in info:
    print(col)


Column Info:
ID, Name, Type, NotNull, DefaultVal, PrimaryKey
(0, 'id', 'INTEGER', 0, None, 1)
(1, 'identifier', 'TEXT', 0, None, 0)
(2, 'filename', 'TEXT', 0, None, 0)
(3, 'filesize', 'INT', 0, None, 0)
(4, 'path', 'TEXT', 0, None, 0)
(5, 'x', 'INT', 0, None, 0)
(6, 'y', 'INT', 0, None, 0)
(7, 'imageformat', 'TEXT', 0, None, 0)
(8, 'creator', 'TEXT', 0, None, 0)


Quick test to retrive one row

In [7]:
c.execute('''
    SELECT * 
    FROM images 
    ORDER BY ROWID ASC 
    LIMIT 1
''')
rows = c.fetchall()
for row in rows:
    print(row)

(1, 'cond-mat0606521', 'lay_f2.eps', 29311, './0606/cond-mat0606521', 250, 180, 'PS', '-')


In [8]:
c.execute('''
    SELECT * 
    FROM metadata 
    ORDER BY ROWID ASC 
    LIMIT 1
''')
rows = c.fetchall()
for row in rows:
    print(row)

(1, '0704.0026', '2007-03-31', 'math.RA', "['de Marrais, Robert P. C.; ']", 'Placeholder Substructures II: Meta-Fractals, Made of Box-Kites, Fill\n  Infinite-Dimensional Skies', '  Zero-divisors (ZDs) derived by Cayley-Dickson Process (CDP) from\nN-dimensional hypercomplex numbers (N a power of 2, at least 4) can represent\nsingularities and, as N approaches infinite, fractals -- and thereby,scale-free\nnetworks. Any integer greater than 8 and not a power of 2 generates a\nmeta-fractal or "Sky" when it is interpreted as the "strut constant" (S) of an\nensemble of octahedral vertex figures called "Box-Kites" (the fundamental\nbuilding blocks of ZDs). Remarkably simple bit-manipulation rules or "recipes"\nprovide tools for transforming one fractal genus into others within the context\nof Wolfram\'s Class 4 complexity.\n', '')


## Writing to org mode

Find a few random entries from both metadata and images, write to org mode

In [ ]:
c.execute('''
    SELECT * 
    FROM metadata 
    ORDER BY RANDOM() 
    LIMIT 3
''')
rows = c.fetchall()
with open("metadata_sample.org", "w+") as write_file:
    print("|", file=write_file, end = '')
    for row in rows:
    #     print(row)
        for item in row:
            print(str(item).replace("\n", " "), file=write_file, end = '')
            print("|", file=write_file, end = '')
        print("\n|", file=write_file, end = '')
write_file.close()

In [ ]:
c.execute('''
    SELECT * 
    FROM images 
    ORDER BY RANDOM() 
    LIMIT 3
''')
rows = c.fetchall()
with open("images_sample.org", "w+") as write_file:
    print("|", file=write_file, end = '')
    for row in rows:
    #     print(row)
        for item in row:
            print(str(item).replace("\n", " "), file=write_file, end = '')
            print("|", file=write_file, end = '')
        print("\n|", file=write_file, end = '')
write_file.close()

## Database Queries

### Find any duplicate identifiers

In [ ]:
# look for duplicate rows in the metadata table
c.execute('''
    SELECT identifier, COUNT(identifier)
    FROM metadata
    GROUP BY identifier
    HAVING COUNT(identifier) > 1
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# look for duplicate rows in the images table (brings up totals for images by article ID)
c.execute('''
    SELECT identifier, COUNT(identifier)
    FROM images
    GROUP BY identifier
    HAVING COUNT(identifier) > 0
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# look for duplicate images (search by filename, filesize, and identifier)
# there is quite a lot of these, but that is how the source data was uploaded
c.execute('''
    SELECT identifier, filename, filesize, path, COUNT(*) c
    FROM images
    GROUP BY identifier, filename, filesize
    HAVING c > 1
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

### Earliest dates

In [ ]:
# Find the earliest date of an article

c.execute('''
    SELECT created, identifier
    FROM metadata
    WHERE created IS NOT NULL
    ORDER BY created ASC
    LIMIT 20
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find the earliest dated articles and get the associated images

c.execute('''
    SELECT images.identifier, metadata.created, metadata.identifier 
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE metadata.created IS NOT NULL
    ORDER BY created ASC
    LIMIT 40
    ''')
    
rows = c.fetchall()
for row in rows:
    print(row)

### Total numbers of articles and images

In [ ]:
# Find total number of rows in metadata

c.execute('''
    SELECT count(*)
    FROM metadata
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find total number of rows in images

c.execute('''
    SELECT count(*)
    FROM images
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find total number of rows in images (filtering out images without size or imageformat)

c.execute('''
    SELECT count(*)
    FROM images
    WHERE x IS NOT null AND x != ''
    AND y IS NOT null AND y != ''
    AND imageformat is not null AND imageformat != ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
print(len(rows))    

### Average image sizes

In [ ]:
# Get average of the x size column

c.execute('''
    SELECT avg(x)
    FROM images
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get average of the y size column

c.execute('''
    SELECT avg(y)
    FROM images
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get median of the x size column

c.execute('''
    SELECT x
    FROM images
    ORDER by x
    LIMIT 1
    OFFSET (SELECT COUNT(*) FROM images) / 2
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get median of the y size column

c.execute('''
    SELECT y
    FROM images
    ORDER by y
    LIMIT 1
    OFFSET (SELECT COUNT(*) FROM images) / 2
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

### Missing fields

In [ ]:
# Find where there are NULL values for x

c.execute('''
    SELECT id, identifier, path, filename, filesize, x, y, imageformat
    FROM images
    WHERE x is null or x = ''
    OR y is null or y = ''
    OR imageformat is null or imageformat = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# generate a text file listing paths of files that couldn't be identified
with open("identify_errors_db.txt", "a+") as f:
    for row in rows[:]:
        filepath = row[2][1:] + "/" + row[3]
        print(str(row[0]) + "," + filepath)
        f.write(str(row[0]) + "," + filepath + "\n")


In [ ]:
print(len(rows))

In [ ]:
# Find where there are NULL values for y

c.execute('''
    SELECT id, identifier, path, filename, filesize, x, y, imageformat
    FROM images
    WHERE y is null or y = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

In [ ]:
# Find where there are NULL values for identifier

c.execute('''
    SELECT id, identifier, path, filesize, x, y, imageformat
    FROM images
    WHERE identifier is null or identifier = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)
    
# no result is a good result!

In [ ]:
# Find where there are NULL values for filesize

c.execute('''
    SELECT id, identifier, path, filesize, x, y, imageformat
    FROM images
    WHERE filesize is null or filesize = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

In [ ]:
# Get number of articles with no category
# this seems to give no results

c.execute('''
    SELECT identifier, cat
    FROM metadata
    WHERE cat IS NULL OR cat = '' OR cat = 'None'
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find where there is no matching metadata for a given image

c.execute('''
    SELECT count(images.identifier), images.identifier
    FROM images
    LEFT JOIN metadata ON metadata.identifier = images.identifier
    WHERE metadata.identifier IS NULL
    GROUP BY images.identifier
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find where there is no identifier for an image

c.execute('''
    SELECT identifier, id, filename, filesize, path, x, y
    FROM images
    WHERE identifier IS NULL OR identifier = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# More looking for specific entries with no identifier

c.execute('''
    SELECT identifier, id
    FROM images
    WHERE identifier IS NULL OR identifier = ''
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(sum(row[0] for row in rows))

### Averages of images

In [ ]:
# Get total number of images per article

c.execute('''
    SELECT images.identifier, metadata.cat, count(images.identifier)    
    FROM images 
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY images.identifier
    ORDER BY count(images.identifier)
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get total number of images per category

c.execute('''
    SELECT metadata.cat, count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY metadata.cat
    ORDER BY count(images.identifier) DESC    
    LIMIT 200
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get total number of images per primary category only

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1), count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1)
    ORDER BY count(images.identifier) DESC    
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# write text file

fname = "stats_images_by_category.txt"
f = open(fname, "w+")
for row in rows:
    f.write(row[0] + ", " + str(row[1]) + "\n")
f.close()

In [ ]:
print(len(rows))

In [ ]:
# Get total number of images per primary category only - with a specific filter

c.execute('''
    SELECT substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1), count(images.identifier)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1) = "cond-mat.mes-hall"
    GROUP BY substr(trim(metadata.cat),1,instr(trim(metadata.cat)||' ',' ')-1)
    ORDER BY count(images.identifier) DESC    
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

### Totals by month/year

In [ ]:
# Find number of articles by year

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of articles in each month/year

c.execute('''
    SELECT count(metadata.identifier), strftime("%m-%Y", metadata.created) as 'mY'
    FROM metadata
    GROUP BY strftime("%m-%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of images by year

c.execute('''
    SELECT count(images.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of images in each month/year

c.execute('''
    SELECT count(images.identifier), strftime("%m-%Y", metadata.created) as 'mY'
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier 
    GROUP BY strftime("%m-%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
total = 0
for row in rows:
    total += row[0]
print(total)

#### ...and by category

In [ ]:
# Find number of articles by year by category

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    WHERE substr(trim(cat),1,instr(trim(cat)||' ',' ')-1) = 'cs.CV'
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Find number of articles by year by category, for a specific query

c.execute('''
    SELECT count(metadata.identifier), strftime("%Y", metadata.created) as 'Y'
    FROM metadata
    WHERE substr(trim(cat),1,instr(trim(cat)||' ',' ')-1) = 'cs.CV'
    AND strftime("%Y", metadata.created) = '2018'
    GROUP BY strftime("%Y", metadata.created)
    ORDER BY strftime("%Y", metadata.created) ASC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
print(len(rows))

In [ ]:
# values = np.array()
values = [item[0] for item in rows]
plt.plot(values)

### Other metadata

In [ ]:
# Find number of images per each different imageformat

c.execute('''
    SELECT imageformat, count(imageformat)
    FROM images
    GROUP BY imageformat
    ORDER BY count(imageformat) DESC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get only the first listed category

c.execute('''
    SELECT identifier, cat, substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)
    FROM metadata
    LIMIT 20
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the licence information for number of articles

c.execute('''
    SELECT licence, COUNT(licence)
    FROM metadata
    GROUP BY licence
    HAVING COUNT(identifier) > 0
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per licence

c.execute('''
    SELECT metadata.licence, COUNT(metadata.licence)
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    GROUP BY metadata.licence
    HAVING COUNT(images.identifier) > 0
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get number of articles for each primary category

c.execute('''
    SELECT count(substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)), substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)
    FROM metadata
    GROUP BY substr(trim(cat),1,instr(trim(cat)||' ',' ')-1)
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

### Querying by image extension

In [ ]:
# define reverse function
db.create_function("reverse", 1, lambda s: s[::-1])

In [ ]:
# Get the number of images per extension
# DON'T filter based on X or Y dimension

c.execute('''
    SELECT COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1))), reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension
    FROM images
    GROUP BY extension 
    ''')

rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per extension
# filter based on X or Y dimension

c.execute('''
    SELECT COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1))), reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension
    FROM images
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    GROUP BY extension
    ''')

rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per extension by year
# filter based on X or Y dimension
# 2018 only

c.execute('''
    SELECT reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension, COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)))
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    AND strftime("%Y", metadata.created) = '2018'
    GROUP BY extension
    ''')

rows = c.fetchall()
for row in rows:
    print(row)

In [ ]:
# Get the number of images per extension
# filter based on X or Y dimension

c.execute('''
    SELECT reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension, COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)))
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    GROUP BY extension
    ''')

rows = c.fetchall()
for row in rows:
    print(row)
    
total = 0
for row in rows:
    total += row[1]
print("total:", total)

print("*" * 20)

alldata = []
for i, row in enumerate(rows):
    alldata.append([row[0], row[1], row[1]/total])
for d in alldata:
    print("{} | {} | {:2.2%}".format(d[0], d[1], d[2]))

### Get extensions by years and get statistics for changing percentages

In [ ]:
# Get list of years

c.execute('''
    SELECT strftime("%Y", metadata.created), COUNT(strftime("%Y", metadata.created))
    FROM metadata
    GROUP BY strftime("%Y", metadata.created)
    ''')

years = []

rows = c.fetchall()
for row in rows:
    print(row)
    years.append(row[0])
print(years)

In [ ]:
# Get the number of images per extension by year
# filter based on X or Y dimension

data = []

# manually selecting years
# years = ["2000", "2005", "2010", "2015"]

db.create_function("reverse", 1, lambda s: s[::-1])
sql = ('''
    SELECT reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)) AS extension, COUNT(reverse(substr(reverse(filename),1,instr(reverse(filename),'.')-1)))
    FROM images
    LEFT JOIN metadata ON images.identifier = metadata.identifier
    WHERE x is not null and x != ''
    AND y is not null and y != ''
    AND imageformat is not null and imageformat != ''
    AND strftime("%Y", metadata.created) = ?
    GROUP BY extension
    ''')

# data = []

for y, year in enumerate(years):
    print("*" * 20)
    print(year)
    print("*" * 20)
    c.execute(sql, (year, ))

    rows = c.fetchall()
#     for row in rows:
#         print(row)
    total = 0
    for row in rows:
        total += row[1]
    print("total:", total)

    data = []
    for i, row in enumerate(rows):
        data.append([row[0], row[1], row[1]/total])
    for d in data:
        print("{} | {} | {:2.2%}".format(d[0], d[1], d[2]))
#     print(data)
        

In [ ]:
for d in data:
    print(d)

In [ ]:
# get proportion as percentage

total = 0
for row in rows:
    total += row[1]
print(total)

data = []
for row in rows:
    data.append([row[0], row[1], row[1]/total])
print(data)

In [ ]:
# take second element for sort
def takeSecond(elem):
    return elem[1]
data.sort(key=takeSecond)

for d in data:
    print("{} | {} | {:2.2%}".format(d[0], d[1], d[2]))

In [ ]:
values = []
names = []
for row in rows:
    values.append(row[0])
    names.append(row[1])

In [ ]:
values_save = values
names_save = names

In [ ]:
for i, name in enumerate(names.copy()):
    names[i] = name.lower()
print(names)

In [ ]:
print(values)
print(names)
print(len(values))
print(len(names))

In [ ]:
total = 0
for row in rows:
    total += row[0]
print(total)

In [ ]:
# writing file to org mode for github

# write the data to a file
with open("stats_articles_by_cat.org", "w") as write_file:
    print("* number of articles by category", file=write_file)
    print("|-|-|", file=write_file)
    for cat in rows:
#         joined = list(zip(cat[1], cat[2]))
        #     print(joined)
        print('|' + str(cat[0]) + "|" + str(cat[1]) + "|", file=write_file)
    print("|-|-|", file=write_file)
write_file.close()

#### Image metadata

In [13]:
# Get the number of images per licence

c.execute('''
    SELECT images.creator, COUNT(images.creator)
    FROM images
    GROUP BY images.creator
    ORDER BY COUNT(images.creator) DESC
    ''')
rows = c.fetchall()
for row in rows:
    print(row)

('-', 1954941)
('SM', 267700)
('TeX', 207549)
('OriginLab Corporation', 168350)
('GIMP PostScript file plugin V 1.17 by Peter Kirchgessner', 142514)
('MATLAB, The Mathworks, Inc.', 132161)
('Mathematica', 123598)
('R', 97955)
('ImageMagick', 92091)
('MATLAB, The MathWorks, Inc.', 80290)
('fig2dev Version 3.2 Patchlevel 4', 74206)
('jpeg2ps V1.9 by Thomas Merz', 73445)
('PGPLOT', 69804)
('cairo 1.10.2 (http://cairographics.org)', 68873)
('gnuplot 4.0 patchlevel 0', 65872)
('Grace-5.1.22', 64234)
('PGPLOT [PSDRIV 6.6]', 57288)
('PScript5.dll Version 5.2.2', 57154)
('fig2dev Version 3.2 Patchlevel 3d', 52530)
('matplotlib 1.5.1, http://matplotlib.org', 50239)
('cairo 1.12.16 (http://cairographics.org)', 49695)
('matplotlib 1.3.1, http://matplotlib.org', 46416)
('R Software', 45079)
('', 42516)
('cairo 1.13.1 (http://cairographics.org)', 39796)
('matplotlib 2.0.2, http://matplotlib.org', 35701)
('Adobe Illustrator(R) 16.0', 33964)
('cairo 1.14.0 (http://cairographics.org)', 33417)
('cairo 

('Adobe Photoshop Version 8.0x354', 48)
('Artem', 48)
('Asif Khan', 48)
('Atreides', 48)
('Ben@LEVEQUE (U-LEVEQUE\\Ben,S-1-5-21-36325834-85256344-3924636773-1000)', 48)
('Celia Reina Romo', 48)
('Christian with JaxoDraw-1.3-2', 48)
('CorelDRAW Home & Student X7', 48)
('G900TUVS1GPI1', 48)
('GL2PS 1.1.2, (C) 1999-2003 Christophe Geuzaine <geuz@geuz.org>', 48)
('GLE 4.2.3 <www.gle-graphics.org>', 48)
('IDL Version 5.0 (AIX ibmr2)', 48)
('Ipe 7.0.9', 48)
('Ivan', 48)
('Javier Piqueras López', 48)
('Jozef Dudek', 48)
('KDE 3.4.0-6 Red Hat', 48)
('KDE 3.5.4-25.el5_4.1 Red Hat', 48)
('KDE 4.14.9', 48)
('KaleidaGraph: LaserWriter 8 8.4.1', 48)
('MATLAB, The MathWorks, Inc. Version 7.11.0.584 (R2010b). Operating System: Darwin 10.7.0 Darwin Kernel Version 10.7.0: Sat Jan 29 15:16:10 PST 2011; root:xnu-1504.9.37~1/RELEASE_X86_64 x86_64.', 48)
('MATLAB, The MathWorks, Inc. Version 7.11.0.584 (R2010b). Operating System: Linux 2.6.32-32-generic #62-Ubuntu SMP Wed Apr 20 21:52:38 UTC 2011 x86_64.',

('G for Linux version #1 SMP Fri Jan 28 13:38:00 CET 2005 release 2.6.8-mexler-2.0', 27)
('GP.EXE (PS driver v3.0)', 27)
('Ghostscript ps2eps from', 27)
('Grab: cgpdftops CUPS filter', 27)
('GraphicConverter V5.3 X', 27)
('Gri2.12.7 (released 2003-Sep-04).  User=vvskokov', 27)
('Guillaume Drion', 27)
('HIGZ Version 1.13/03', 27)
('HIGZ Version 1.23/05', 27)
('Hao Li', 27)
('IDL Version 5.1.1 (IRIX mipseb)', 27)
('IDL Version 5.6 (AIX ibmr2 m64)', 27)
('IDL Version 6.2 (IRIX mipseb m64)', 27)
('IDL Version 7.0.1 (linux x86_64 m64)', 27)
('Ilmo with JaxoDraw-1.3-2', 27)
('ImageMagick 6.6.6', 27)
('IslandDraw for boyland', 27)
('IslandDraw for krueger', 27)
('Jasper', 27)
('Javier Galan,,,', 27)
('Jeff,,,', 27)
('Jie Chen', 27)
('Jimmy', 27)
('KDE 3.5.5', 27)
('KaleidaGraph 3.0.1: LaserWriter 8 8.1.1', 27)
('KaleidaGraph2.1: LaserWriter 8 E1-8.3.3', 27)
('Karbon14 EPS Exportfilter 0.5', 27)
('Karen Vogtmann', 27)
('Kip Thorne', 27)
('LCotton', 27)
('LLK', 27)
('Lloyd T. Elliott and Yee Wh

('Kenan Elibol', 16)
('Kimia', 16)
('Kuleczka with JaxoDraw-1.3-1', 16)
('LaTeX with acmart 2018/04/14 v1.53 Typesetting articles for the Association for Computing Machinery and hyperref 2017/03/14 v6.85a Hypertext links for LaTeX', 16)
('Lazar Berbakov', 16)
('Lehum with JaxoDraw-1.3-2', 16)
('Levent', 16)
('Lingfei', 16)
('Lionel Vincent', 16)
('LiuHao@LIUHAO-THINKPAD, E:\\ligo\\blind_tpl', 16)
('Lucas Goehring', 16)
('Luu, Thomas C.', 16)
('M&M', 16)
('M.C.   Cautun,187, 4087', 16)
('MATLAB, The MathWorks, Inc. Version 7.11.0.584 (R2010b). Operating System: Darwin 11.0.1 Darwin Kernel Version 11.0.1: Thu Jul 28 02:01:39 PDT 2011; root:xnu-1699.23.4~1/RELEASE_X86_64 x86_64.', 16)
('MATLAB, The MathWorks, Inc. Version 7.11.0.584 (R2010b). Operating System: Darwin 13.4.0 Darwin Kernel Version 13.4.0: Mon Jan 11 18:17:34 PST 2016; root:xnu-2422.115.15~1/RELEASE_X86_64 x86_64.', 16)
('MATLAB, The MathWorks, Inc. Version 7.11.0.584 (R2010b). Operating System: Linux 2.6.18-194.26.1.el5 #1 

('jnwang', 12)
('jo@kaas with xmgr', 12)
('johannesk', 12)
('jonatan@desktop, /home/jonatan/mrk178/IZw18/IZw18_2', 12)
('joseabel@uirapuru.ifi.unicamp.br with xmgr', 12)
('joshi@sun1 with xmgr', 12)
('jpark@arecibo, /home/jpark/idl/reionization/semianalytic/project02', 12)
('jpmor', 12)
('jrl', 12)
('jrpelaez', 12)
('jsantiago with JaxoDraw-2.1-0', 12)
('jschmidt', 12)
('jsilv@Workie, /Users/jsilv/BSNIP/late_time', 12)
('jstilck@primobolan with xmgr', 12)
('jsun', 12)
('jtobin@phoenix, /export/data_1/jtobin/tscpvplot', 12)
('julien@avignon.boulder.swri.edu,', 12)
('jund', 12)
('junhua fang', 12)
('jurusik', 12)
('jw', 12)
('jyyong Sohn', 12)
('kaiyu yang', 12)
('kamenev@boubou with xmgr', 12)
('kaplot 1.2.0', 12)
('kasdeya', 12)
('kathrin', 12)
('katz', 12)
('kav@IGAM14WS, /home/kav/new15Feb2011/aia', 12)
('kawasaki', 12)
('kay', 12)
('kb', 12)
('kbidzhie', 12)
('kborm', 12)
('kcovey@Kevins-Mac-Pro.local,', 12)
('khomenko@elche, /scratch1/lena/articles/rti_sim', 12)
('kiefer@quake, /ne

...

('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.7.10-1.36-desktop #1 SMP PREEMPT Thu Jun 12 10:14:12 UTC 2014 (fcb6f8f) x86_64.', 1)
('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.7.6-gentoo #5 SMP Thu Nov 21 14:42:37 CET 2013 x86_64.', 1)
('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.8.0-31-generic #46~precise1-Ubuntu SMP Wed Sep 11 18:21:16 UTC 2013 x86_64.', 1)
('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.8.11-100.fc17.x86_64 #1 SMP Wed May 1 19:31:26 UTC 2013 x86_64.', 1)
('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.8.13-100.fc17.x86_64 #1 SMP Mon May 13 13:36:17 UTC 2013 x86_64.', 1)
('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Operating System: Linux 3.9.9-302.1m.el6.x86_64 #1 SMP Tue Jul 16 16:34:12 EDT 2013 x86_64.', 1)
('MATLAB, The MathWorks, Inc. Version 8.1.0.604 (R2013a). Op

('VectorWorks', 1)
('VectorWorks 12.0.0', 1)
('Vectorworks 2013 SP5 [18.0.5(209073)]', 1)
('Veena Choithani', 1)
('Veit;Christian', 1)
('Veljko Pejovic', 1)
('Vellum: LaserWriter 8.0 8.0', 1)
('Venkat Viswanathan', 1)
('Venkatesh Saligrama', 1)
('Venkatraman, Ramakrishnan [E CPE]', 1)
('Ver 0.25 x', 1)
('Ver 1.0', 1)
('Ver 2.05SG', 1)
('Ver.1.02e', 1)
('Ver.1.10e', 1)
('Ver.1.3', 1)
('Ver.1.4', 1)
('Ver.2.00D', 1)
('Ver.2.01', 1)
('Ver.2.02', 1)
('Ver.2.2', 1)
('Ver1.00', 1)
('Ver:1.2.06', 1)
('Vera Bendkowsky, Björn Butscher, Johannes Nipper, James P. Shaffer, Robert Löw, Tilman Pfau', 1)
('Vera Hoffmeister', 1)
('Vera Hollink', 1)
('Vered Rom', 1)
('Verena', 1)
('Vergleich 2.xls', 1)
('Verma A. K., Fienga A., Laskar J., Issautier K., Manche H., Gastineau M.', 1)
('Verne\\Admin (VERNE)', 1)
('Verner Thorsmolle', 1)
('Veronique Petit', 1)
('Version 1.0070', 1)
('Version 1.3', 1)
('Version 1.5', 1)
('Versão de Avaliação do Microsoft® PowerPoint® 2010', 1)
('Veusz 1.11.0.3-ppa-daily-2011

('fiolet@danlas, /home/danlas1NS/fiolet/IRS/L31', 1)
('fiolet@danlas, /home/danlas1NS/fiolet/IRS/L33', 1)
('fiolet@danlas, /home/danlas1NS/fiolet/IRS/L5', 1)
('fiolet@danlas, /home/danlas1NS/fiolet/IRS/L7', 1)
('fiolet@danlas, /home/danlas1NS/fiolet/IRS/L9', 1)
('fiona', 1)
('fiore@ciop.dsf.unica.it with xmgr', 1)
('fiore@darkstar with xmgr', 1)
('fiorenti', 1)
('firf1.cpp', 1)
('firfig1d.cpp', 1)
('firfig2c.cpp', 1)
('firfig3c.cpp', 1)
('firfig5b.cpp', 1)
('fishstar with JaxoDraw-2.0-1', 1)
('fissel@Lauras-MacBook-Pro-2.local,', 1)
('fissel@Lauras-MacBook-Pro.local,', 1)
('fit (file version number 58)', 1)
('fits2ps (c) 1998 by L. Balona', 1)
('fivemice', 1)
('fjanuario', 1)
('fjma', 1)
('fjmc', 1)
('fjnu-yrc', 1)
('fkahlhoe with JaxoDraw-2.0-1', 1)
('fkm@tiziu.local (Flavio Keidi Miyazawa)', 1)
('fkuhn@alces \\(Fabian Daniel Kuhn\\)', 1)
('fkuhn@alces \\(Fabian Kuhn\\)', 1)
('flacasa@glx-planck, /home/flacasa/sehgal', 1)
('flad@kopernikus with xmgr', 1)
('flataup', 1)
('flavio@Maca \

('nalbach@hardy with xmgr', 1)
('namiki', 1)
('namo', 1)
('namurphy@spacemoose,', 1)
('nanab64@mai-pc0031.mai.liu.se (ancy Abdallah)', 1)
('nancy', 1)
('nancyagg@outlook.com', 1)
('nancyjia', 1)
('nanditha', 1)
('nando,,,', 1)
('nanl', 1)
('naoto', 1)
('naoya_okamoto', 1)
('napellido', 1)
('naples@farfalle.phyast.pitt.edu (onna Naples)', 1)
('naples@localhost.localdomain (onna Naples)', 1)
('narayan@unknownb88d120fd79e.att.net (Onuttom Narayan)', 1)
('narbe', 1)
('nardi', 1)
('naresh', 1)
('narnaud@yakut01 (icolas Arnaud)', 1)
('nas', 1)
('naseemr@casamacpronr,', 1)
('nasirov', 1)
('nasm3', 1)
('naso@i907, /u/ap/naso/lustre/all/vis', 1)
('nassiri', 1)
('nata@null-60c547025d5a.ccis.ualberta.ca,', 1)
('nata@resnet-34-92.resnet.ucsb.edu,', 1)
('natafhenri-claude@lgit-1112.obs.ujf-grenoble.fr (Nataf Henri-Claude)', 1)
('nataliazywucka', 1)
('natanaelccosta', 1)
('natanaelpc2', 1)
('natasha@ophiuchus, /home/natasha/nasa_2011/apr142002/new_times', 1)
('natasha@rome, /home/natasha/nasa_2011/a

('yanjun', 1)
('yanny', 1)
('yanwen@Eulerian-Odd.local (Yanwen Shang)', 1)
('yanzhang@mathstation020.mit.edu (Yan Zhang)', 1)
('yaodl with JaxoDraw-2.0-1', 1)
('yaojianping', 1)
('yaosu', 1)
('yaoyaoyan', 1)
('yaqin_zhou', 1)
('yara@bimba.oapd.inaf.it, /home/yara/Desktop/CL_vel_disp', 1)
('yaroslav', 1)
('yaser with JaxoDraw-2.1-0', 1)
('yasiriqbal', 1)
('yasmine', 1)
('yasser', 1)
('yasuko', 1)
('yasuo.tabei', 1)
('yasuo@ksoken2 with xmgr', 1)
('yawoo', 1)
('ybj109', 1)
('ybz-ict', 1)
('ychen@ept (ong Chen,128 Clark Hall,607-255-6025,)', 1)
('ychi@ychi-690 \\(Yun Chi\\)', 1)
('yckim@fuslw020, /home/yckim/For_BES_report/DPhil_Thesis', 1)
('yckim@fuslw027,', 1)
('ycliang@dhcp-192-033-102-109.ethz.ch (Yeong-Cherng Liang)', 1)
('ycu@ubuntu, /home/ycu/Data/UV_SSI', 1)
('ycyang with JaxoDraw-1.1-0', 1)
('yd', 1)
('ydiao', 1)
('ydshen', 1)
('ydshen@ydshen-2.local, /Users/ydshen/data/20120423_2', 1)
('ydz', 1)
('ye0003ao', 1)
('yenyo@yenyo-PC4 (U-yenyo-PC4\\yenyo,S-1-5-21-1162113195-174677477

In [21]:
print("|-|-|-|")
for row in rows[1:16]:
    per = str(round((row[1]/10053059*100), 2))
    print("|" + per + "|" + str(row[1]) + "|" + row[0] + '|')
print("|-|-|-|")

|-|-|-|
|2.66|267700|SM|
|2.06|207549|TeX|
|1.67|168350|OriginLab Corporation|
|1.42|142514|GIMP PostScript file plugin V 1.17 by Peter Kirchgessner|
|1.31|132161|MATLAB, The Mathworks, Inc.|
|1.23|123598|Mathematica|
|0.97|97955|R|
|0.92|92091|ImageMagick|
|0.8|80290|MATLAB, The MathWorks, Inc.|
|0.74|74206|fig2dev Version 3.2 Patchlevel 4|
|0.73|73445|jpeg2ps V1.9 by Thomas Merz|
|0.69|69804|PGPLOT|
|0.69|68873|cairo 1.10.2 (http://cairographics.org)|
|0.66|65872|gnuplot 4.0 patchlevel 0|
|0.64|64234|Grace-5.1.22|
|-|-|-|
